In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import random
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn import datasets
from sklearn.metrics import confusion_matrix, accuracy_score
from pytorch_tabnet.tab_model import TabNetClassifier
from sklearn.preprocessing import MinMaxScaler


c:\venv_python_3.10\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
import xgboost as xgb
import lightgbm as lgbm
import catboost as cbt
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV

# Iris Dataset

In [20]:
# import some data to play with
iris = datasets.load_iris()
# Take the first two features. We could avoid this by using a two-dim dataset
# X = iris.data[:, :2]
# y = iris.target


X = iris.data[:, :2]
y = iris.target

In [21]:
x_train, x_test, y_train, y_test = train_test_split(X, y, random_state=4096)

In [22]:
scaler = MinMaxScaler()

scaler = scaler.fit(x_train)


In [23]:
x_train = scaler.transform(x_train)
x_test = scaler.transform(x_test)

In [24]:
# data = np.hstack([raw_df.values[::2, :], raw_df.values[1::2, :2]])
# target = raw_df.values[1::2, 2]
# x_train, x_test, y_train, y_test = train_test_split(data, target, random_state=4096)

# SVM - Linear

In [25]:

svm_classifier = SVC(kernel='linear')
svm_classifier = svm_classifier.fit(x_train, y_train)

In [26]:
y_pred = svm_classifier.predict(x_test)

confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 0,  8, 10],
       [ 0,  1,  8]], dtype=int64)

# SVM - Kernel

In [27]:
param_grid = [
    {'kernel': ['linear'], 'C': [10., 30., 100., 300., 1000., 3000., 10000., 30000.0]},
    {'kernel': ['rbf'], 'C': [1.0, 3.0, 10., 30., 100., 300., 1000.0],
                        'gamma': [0.01, 0.03, 0.1, 0.3, 1.0, 3.0]},
]

In [28]:

svm_classifier = SVC(kernel='rbf')
# svm_classifier = svm_classifier.fit(x_train, y_train)

grid_search = GridSearchCV(svm_classifier, param_grid, cv=5, scoring="neg_mean_squared_error", verbose=2)
best_svm_classifier = grid_search.fit(x_train, y_train)



Fitting 5 folds for each of 50 candidates, totalling 250 fits
[CV] END ..............................C=10.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=10.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=10.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=10.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=10.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=30.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=30.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=30.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=30.0, kernel=linear; total time=   0.0s
[CV] END ..............................C=30.0, kernel=linear; total time=   0.0s
[CV] END .............................C=100.0, kernel=linear; total time=   0.0s
[CV] END .............................C=100.0, 

In [29]:
grid_search.best_params_


{'C': 3.0, 'gamma': 0.3, 'kernel': 'rbf'}

In [30]:
# y_pred = svm_classifier.predict(x_test)
y_pred = best_svm_classifier.predict(x_test)

confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 0, 11,  7],
       [ 0,  1,  8]], dtype=int64)

In [31]:
accuracy_score(y_test, y_pred)

0.7894736842105263

In [116]:
len(y_pred)

38

# TabNet

In [55]:
tabnet_classifier = TabNetClassifier()
# clf = TabNetMultiTaskClassifier()
tabnet_classifier.fit(
  X_train=x_train, y_train=y_train,
  eval_set = [(x_test, y_test)],
  patience=1000,
  max_epochs=200,
  batch_size=8,
)

c:\venv_python_3.10\lib\site-packages\pytorch_tabnet\abstract_model.py:75: UserWarning: Device used : cuda
  warnings.warn(f"Device used : {self.device}")


epoch 0  | loss: 1.02315 | val_0_accuracy: 0.23684 |  0:00:01s
epoch 1  | loss: 0.73632 | val_0_accuracy: 0.23684 |  0:00:02s
epoch 2  | loss: 0.73422 | val_0_accuracy: 0.23684 |  0:00:03s
epoch 3  | loss: 0.62178 | val_0_accuracy: 0.34211 |  0:00:05s
epoch 4  | loss: 0.64264 | val_0_accuracy: 0.31579 |  0:00:06s
epoch 5  | loss: 0.64673 | val_0_accuracy: 0.26316 |  0:00:07s
epoch 6  | loss: 0.63839 | val_0_accuracy: 0.28947 |  0:00:09s
epoch 7  | loss: 0.59684 | val_0_accuracy: 0.28947 |  0:00:10s
epoch 8  | loss: 0.53977 | val_0_accuracy: 0.36842 |  0:00:11s
epoch 9  | loss: 0.61046 | val_0_accuracy: 0.26316 |  0:00:13s
epoch 10 | loss: 0.60604 | val_0_accuracy: 0.42105 |  0:00:14s
epoch 11 | loss: 0.56897 | val_0_accuracy: 0.55263 |  0:00:15s
epoch 12 | loss: 0.56469 | val_0_accuracy: 0.44737 |  0:00:16s
epoch 13 | loss: 0.5639  | val_0_accuracy: 0.52632 |  0:00:17s
epoch 14 | loss: 0.55126 | val_0_accuracy: 0.71053 |  0:00:19s
epoch 15 | loss: 0.58645 | val_0_accuracy: 0.76316 |  0

c:\venv_python_3.10\lib\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


In [56]:
y_pred = tabnet_classifier.predict(x_test)


confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 0, 12,  6],
       [ 0,  1,  8]], dtype=int64)

# XGBoost

In [94]:
num_round = 3
xgb_classifier = xgb.XGBClassifier()

xgb_parameters ={'max_depth' : [3,4,5,6] , 'n_estimators': [12,24,32], 'learning_rate':[0.01, 0.1], 'gamma': [0.5, 1, 2], 'random_state':[99]}

In [95]:
# xgb_classifier=xgb_classifier.fit(x_train, y_train)

xgb_grid_search = GridSearchCV(xgb_classifier, xgb_parameters, cv=5, scoring="neg_mean_squared_error", verbose=2)
best_xgb_classifier = xgb_grid_search.fit(x_train, y_train)

Fitting 5 folds for each of 72 candidates, totalling 360 fits
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=12, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=12, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=12, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=12, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=12, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=24, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=24, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=24, random_state=99; total time=   0.0s
[CV] END gamma=0.5, learning_rate=0.01, max_depth=3, n_estimators=24, random_state=99; tot

In [96]:

xgb_grid_search.best_params_

{'gamma': 1,
 'learning_rate': 0.01,
 'max_depth': 3,
 'n_estimators': 12,
 'random_state': 99}

In [97]:
# y_pred = xgb_classifier.predict(x_test)
y_pred = best_xgb_classifier.predict(x_test)


confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 1, 10,  7],
       [ 0,  1,  8]], dtype=int64)

# LightGBM

In [68]:
num_round = 3
lgbm_classifier = lgbm.LGBMClassifier()

In [69]:
lgbm_classifier=lgbm_classifier.fit(x_train, y_train)

In [70]:

y_pred = lgbm_classifier.predict(x_test)


confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 0, 10,  8],
       [ 0,  1,  8]], dtype=int64)

# CatBoost

In [71]:
num_round = 3
cbt_classifier = cbt.CatBoostClassifier()

In [101]:
cbt_parameters = {'depth'         : [4,5,6,7,8,9, 10],
                'learning_rate' : [0.01,0.02,0.03,0.04],
                'iterations'    : [10, 20,30,40,50,60,70,80,90, 100]
}

In [102]:
# cbt_classifier=cbt_classifier.fit(x_train, y_train)

cbt_grid_search = GridSearchCV(cbt_classifier, cbt_parameters, cv=5, scoring="neg_mean_squared_error", verbose=2)
best_cbt_classifier = cbt_grid_search.fit(x_train, y_train)

Fitting 5 folds for each of 280 candidates, totalling 1400 fits
0:	learn: 1.0933598	total: 856us	remaining: 7.71ms
1:	learn: 1.0859074	total: 1.44ms	remaining: 5.75ms
2:	learn: 1.0793046	total: 1.99ms	remaining: 4.64ms
3:	learn: 1.0723663	total: 2.51ms	remaining: 3.77ms
4:	learn: 1.0667482	total: 3.01ms	remaining: 3.01ms
5:	learn: 1.0605631	total: 3.52ms	remaining: 2.35ms
6:	learn: 1.0536692	total: 3.99ms	remaining: 1.71ms
7:	learn: 1.0485452	total: 4.49ms	remaining: 1.12ms
8:	learn: 1.0424313	total: 4.95ms	remaining: 549us
9:	learn: 1.0378762	total: 5.41ms	remaining: 0us
[CV] END .........depth=4, iterations=10, learning_rate=0.01; total time=   0.0s
0:	learn: 1.0931913	total: 673us	remaining: 6.06ms
1:	learn: 1.0860581	total: 1.27ms	remaining: 5.1ms
2:	learn: 1.0804519	total: 1.96ms	remaining: 4.57ms
3:	learn: 1.0733881	total: 2.51ms	remaining: 3.76ms
4:	learn: 1.0680082	total: 3.04ms	remaining: 3.04ms
5:	learn: 1.0620500	total: 3.42ms	remaining: 2.28ms
6:	learn: 1.0554518	total: 3.8

In [107]:
cbt_grid_search.best_params_

{'depth': 5, 'iterations': 100, 'learning_rate': 0.04}

In [108]:
# y_pred = cbt_classifier.predict(x_test)
y_pred = best_cbt_classifier.predict(x_test)

confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 0, 10,  8],
       [ 0,  1,  8]], dtype=int64)

# Random Forest

In [109]:
rf_param_grid = { 
    'n_estimators': [200, 500],
    'max_features': ['auto', 'sqrt', 'log2'],
    'max_depth' : [4,5,6,7,8],
    'criterion' :['gini', 'entropy']
}

In [110]:
num_round = 3
rf_classifier = RandomForestClassifier()

rf_grid_search = GridSearchCV(rf_classifier, rf_param_grid, cv=5, scoring="neg_mean_squared_error", verbose=2)
best_rf_classifier = rf_grid_search.fit(x_train, y_train)



Fitting 5 folds for each of 60 candidates, totalling 300 fits


c:\venv_python_3.10\lib\site-packages\sklearn\ensemble\_forest.py:427: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(


[CV] END criterion=gini, max_depth=4, max_features=auto, n_estimators=200; total time=   0.2s


c:\venv_python_3.10\lib\site-packages\sklearn\ensemble\_forest.py:427: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(


[CV] END criterion=gini, max_depth=4, max_features=auto, n_estimators=200; total time=   0.2s


...

c:\venv_python_3.10\lib\site-packages\sklearn\ensemble\_forest.py:427: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(


[CV] END criterion=entropy, max_depth=8, max_features=auto, n_estimators=500; total time=   0.3s


c:\venv_python_3.10\lib\site-packages\sklearn\ensemble\_forest.py:427: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(


[CV] END criterion=entropy, max_depth=8, max_features=auto, n_estimators=500; total time=   0.3s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=200; total time=   0.0s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=200; total time=   0.0s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=200; total time=   0.0s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=200; total time=   0.0s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=200; total time=   0.0s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=500; total time=   0.3s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=500; total time=   0.3s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=500; total time=   0.3s
[CV] END criterion=entropy, max_depth=8, max_features=sqrt, n_estimators=500; total time=   0.3s
[CV] END criterion=entropy, ma

c:\venv_python_3.10\lib\site-packages\sklearn\ensemble\_forest.py:427: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(


In [111]:
# rf_classifier = rf_classifier.fit(x_train, y_train)

In [112]:
best_rf_classifier.best_params_

{'criterion': 'entropy',
 'max_depth': 5,
 'max_features': 'auto',
 'n_estimators': 200}

In [113]:

y_pred = best_rf_classifier.predict(x_test)

confusion_matrix(y_test, y_pred)

array([[11,  0,  0],
       [ 0,  9,  9],
       [ 0,  1,  8]], dtype=int64)